# 特征工程（制作特征和标签，转成监督学习问题）

我们先捋一下基于原始的给定数据， 有哪些特征可以直接利用：

1. 文章的自身特征，`category_id` 表示这文章的类型，`created_at_ts` 表示文章建立的时间，这个关系着文章的时效性，`words_count` 是文章的字数，一般字数太长我们不太喜欢点击, 也不排除有人就喜欢读长文。
2. 文章的内容 `embedding` 特征，这个召回的时候用过，这里可以选择使用，也可以选择不用，也可以尝试其他类型的 `embedding` 特征，比如 W2V 等
3. 用户的设备特征信息

上面这些直接可以用的特征，待做完特征工程之后，直接就可以根据 `article_id` 或者是 `user_id` 把这些特征加入进去。但是我们需要先基于召回的结果，构造一些特征，然后制作标签，形成一个监督学习的数据集。

构造监督数据集的思路，根据召回结果，我们会得到一个 {user_id: [可能点击的文章列表]} 形式的字典。那么我们就可以对于每个用户，每篇可能点击的文章构造一个监督测试集，比如对于用户 user1，假设得到的他的召回列表 {user1: [item1, item2, item3]} ，我们就可以得到三行数据 (user1, item1), (user1, item2), (user1, item3) 的形式，这就是监督测试集时候的前两列特征。

构造特征的思路是这样，我们知道每个用户的点击文章是与其历史点击的文章信息是有很大关联的，比如同一个主题、相似等等。所以特征构造这块很重要的一系列特征<font color=red>是要结合用户的历史点击文章信息</font>。我们已经得到了每个用户及点击候选文章的两列的一个数据集，而我们的目的是要预测最后一次点击的文章，比较自然的一个思路就是和其最后几次点击的文章产生关系，这样既考虑了其历史点击文章信息，又得离最后一次点击较近，因为新闻很大的一个特点就是注重时效性。

往往用户的最后一次点击会和其最后几次点击有很大的关联。所以我们就可以对于每个候选文章，做出与最后几次点击相关的特征如下：

1. 候选物品与最后几次点击的相似性特征（embedding 内积）——这个直接关联用户历史行为
2. 候选物品与最后几次点击的相似性特征的统计特征——统计特征可以减少一些波动和异常
3. 候选物品与最后几次点击文章的字数差的特征——可以通过字数看用户偏好
4. 候选物品与最后几次点击的文章建立的时间差特征——时间差特征可以看出该用户对于文章的实时性的偏好   

此外，如果使用了 youtube 召回的话，我们还可以制作用户与候选 item 的相似特征。

当然，上面只是提供了一种基于用户历史行为做特征工程的思路，大家也可以思维风暴一下，尝试一些其他的特征。下面我们就实现上面的这些特征的制作，实现的逻辑是这样：

1. 我们首先获得用户的最后一次点击操作和用户的历史点击，这个基于我们的日志数据集做
2. 基于用户的历史行为制作特征，这个会用到用户的历史点击表，最后的召回列表，文章的信息表和 embedding 向量
3. 制作标签，形成最后的监督学习数据集

## 1 导包

In [2]:
import os
import time
import pickle
import logging
import numpy as np
import pandas as pd
from tqdm import tqdm
import lightgbm as lgb
from gensim.models import Word2Vec
from sklearn.preprocessing import MinMaxScaler

import warnings
warnings.filterwarnings('ignore')

---

## 2 节省内存标准函数

In [3]:
def reduce_mem(df: pd.DataFrame) -> pd.DataFrame:
    """
    减少 DataFrame 的内存使用，优化数据类型。

    Args:
        df (`pd.DataFrame`): 需要优化内存使用的 DataFrame。

    Returns:
        `pd.DataFrame`: 优化后的 DataFrame，内存使用减少。
    """
    starttime = time.time()
    numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
    start_mem = df.memory_usage().sum() / 1024**2  # 初始内存使用量（以 MB 为单位）
    
    for col in df.columns:
        col_type = df[col].dtypes
        if col_type in numerics:
            c_min = df[col].min()  # 列的最小值
            c_max = df[col].max()  # 列的最大值
            if pd.isnull(c_min) or pd.isnull(c_max):
                continue  # 跳过包含 NaN 的列
                
            # 针对整型数据进行优化
            if str(col_type)[:3] == 'int':
                if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
                    df[col] = df[col].astype(np.int16)
                elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
                    df[col] = df[col].astype(np.int64)
            # 针对浮点型数据进行优化
            else:
                if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)
    
    end_mem = df.memory_usage().sum() / 1024**2  # 优化后的内存使用量（以 MB 为单位）
    print('-- Mem. usage decreased to {:5.2f} Mb ({:.1f}% reduction), time spent: {:2.2f} min'.format(
        end_mem,
        100 * (start_mem - end_mem) / start_mem,
        (time.time() - starttime) / 60
    ))
    
    return df

In [4]:
# 定义数据路径
data_path = '../data/'
save_path = '../tmp_results/'

---

## 3 数据读取

### 3.1 训练集和验证集的划分

划分训练和验证集的原因是为了在线下验证模型参数的好坏，为了完全模拟测试集，我们这里就在训练集中抽取部分用户的所有信息来作为验证集。

提前做训练验证集划分的好处就是可以分解制作排序特征时的压力，一次性做整个数据集的排序特征可能时间会比较长。

In [6]:
def train_val_split(all_click_df: pd.DataFrame, sample_user_nums: int) -> tuple:
    """
    将训练集划分为训练集和验证集。

    Args:
        all_click_df (`pd.DataFrame`): 包含所有用户点击数据的 DataFrame，必须包含 'user_id' 和 'click_timestamp' 列。
        sample_user_nums (`int`): 采样作为验证集的用户数量。

    Returns:
        `tuple`: 返回三个元素：
            - `click_trn`: 训练集的 DataFrame。
            - `click_val`: 验证集的 DataFrame。
            - `val_ans`: 验证集的答案（最后一次点击）DataFrame。
    """
    
    all_click = all_click_df
    all_user_ids = all_click.user_id.unique()
    
    # 从所有用户中随机采样指定数量的用户，replace=False表示不重复抽样
    sample_user_ids = np.random.choice(all_user_ids, size=sample_user_nums, replace=False) 
    
    # 根据采样的用户 ID 划分验证集和训练集
    click_val = all_click[all_click['user_id'].isin(sample_user_ids)]
    click_trn = all_click[~all_click['user_id'].isin(sample_user_ids)]
    
    # 将验证集中的最后一次点击抽取出来作为答案
    click_val = click_val.sort_values(['user_id', 'click_timestamp'])
    val_ans = click_val.groupby('user_id').tail(1)
    
    # 去除验证集中每个用户的最后一次点击，得到用于验证的点击数据
    click_val = click_val.groupby('user_id').apply(lambda x: x[:-1]).reset_index(drop=True)
    
    # 确保验证集答案中的用户在验证集中有点击数据，避免冷启动问题
    val_ans = val_ans[val_ans.user_id.isin(click_val.user_id.unique())]  # 保证答案中的用户在验证集中仍然有点击数据
    click_val = click_val[click_val.user_id.isin(val_ans.user_id.unique())]
    
    return click_trn, click_val, val_ans

### 3.2 获取历史点击和最后一次点击

In [7]:
def get_hist_and_last_click(all_click: pd.DataFrame) -> tuple:
    """
    获取用户的历史点击和最后一次点击的信息。

    Args:
        all_click (`pd.DataFrame`): 包含用户点击数据的 DataFrame，必须包含 'user_id' 和 'click_timestamp' 列。

    Returns:
        `tuple`: 返回两个 DataFrame：
            - `click_hist_df`: 用户的历史点击数据（不包括最后一次点击）。
            - `click_last_df`: 用户的最后一次点击数据。
    """
    
    all_click = all_click.sort_values(by=['user_id', 'click_timestamp'])  # 按用户和点击时间排序
    click_last_df = all_click.groupby('user_id').tail(1)  # 获取每个用户的最后一次点击

    # 定义历史点击函数
    def hist_func(user_df):
        if len(user_df) == 1:
            return user_df  # 如果用户只有一个点击，返回该点击
        else:
            return user_df[:-1]  # 否则返回历史点击（去掉最后一次点击）

    # 应用历史点击函数，获取每个用户的历史点击数据
    click_hist_df = all_click.groupby('user_id').apply(hist_func).reset_index(drop=True)

    return click_hist_df, click_last_df

### 3.3 读取训练、验证及测试集


In [8]:
def get_train_val_tst_data(data_path: str, offline: bool = True) -> tuple:
    """
    读取训练集、验证集和测试集的数据。

    Args:
        data_path (`str`): 数据文件路径。
        offline (`bool`): 指定是否使用离线模式。默认为 True。

    Returns:
        `tuple`: 返回四个元素：
            - `click_trn`: 训练集的 DataFrame。
            - `click_val`: 验证集的 DataFrame（离线模式下）。
            - `click_tst`: 测试集的 DataFrame。
            - `val_ans`: 验证集的答案（离线模式下）。
    """
    
    if offline:
        # 读取训练集用户点击日志
        click_trn_data = pd.read_csv(data_path + 'train_click_log.csv')
        click_trn_data = reduce_mem(click_trn_data)  # 减少内存使用
        
        # 划分训练集和验证集
        click_trn, click_val, val_ans = train_val_split(click_trn_data, sample_user_nums)
    else:
        # 读取训练集用户点击日志，离线模式下不进行划分
        click_trn = pd.read_csv(data_path + 'train_click_log.csv')
        click_trn = reduce_mem(click_trn)
        click_val = None
        val_ans = None
    
    # 读取测试集用户点击日志
    click_tst = pd.read_csv(data_path + 'testA_click_log.csv')
    
    return click_trn, click_val, click_tst, val_ans

### 3.4 读取召回列表

In [9]:
def get_recall_list(save_path: str, single_recall_model: str = None, multi_recall: bool = False) -> dict:
    """
    返回多路召回列表或单路召回的结果。

    Args:
        save_path (`str`): 存储召回结果的路径。
        single_recall_model (`str`, optional): 指定单路召回模型的名称。默认为 None。
        multi_recall (`bool`, optional): 指示是否返回多路召回结果。默认为 False。

    Returns:
        `dict`: 返回召回结果的字典，具体内容根据输入参数决定。
    """
    
    if multi_recall:
        # 返回多路召回的结果
        return pickle.load(open(save_path + 'final_recall_items_dict.pkl', 'rb'))
    
    # 根据指定的单路召回模型加载对应的召回结果
    if single_recall_model == 'i2i_itemcf':
        return pickle.load(open(save_path + 'itemcf_recall_dict.pkl', 'rb'))
    elif single_recall_model == 'i2i_emb_itemcf':
        return pickle.load(open(save_path + 'itemcf_emb_dict.pkl', 'rb'))
    elif single_recall_model == 'user_cf':
        return pickle.load(open(save_path + 'youtubednn_usercf_dict.pkl', 'rb'))
    elif single_recall_model == 'youtubednn':
        return pickle.load(open(save_path + 'youtube_u2i_dict.pkl', 'rb'))

### 3.5 读取各种Embedding

#### 3.5.1 Word2Vec

Word2Vec 主要思想是：一个词的上下文可以很好的表达出词的语义。通过无监督学习产生词向量的方式。word2vec 中有两个非常经典的模型：skip-gram 和 cbow。

- skip-gram（跳元模型）：已知中心词预测周围词
- cbow（词袋模型）：已知周围词预测中心词

<img src="../image/word2vec.png">

#### 3.5.2 Gensim

Gensim（generate similarity）是一个简单高效的自然语言处理Python库，用于抽取文档的语义主题（semantic topics）。Gensim的输入是原始的、无结构的数字文本（纯文本），内置的算法包括Word2Vec，FastText，潜在语义分析（Latent Semantic Analysis，LSA），潜在狄利克雷分布（Latent Dirichlet Allocation，LDA）等。

通过计算训练语料中的统计共现模式自动发现文档的语义结构。这些算法都是非监督的，这意味着不需要人工输入——仅仅需要一组纯文本语料。一旦发现这些统计模式后，任何纯文本（句子、短语、单词）就能采用语义表示简洁地表达。

在使用 gensim 训练 word2vec 的时候，有几个比较重要的参数：

1. `vector_size`：表示词向量的维度
2. `window`：决定了目标词会与多远距离的上下文产生关系
3. `sg`：如果是 0，则是 CBOW 模型，是 1 则是 Skip-Gram 模型
4. `workers`：表示训练时候的线程数量
5. `min_count`：需要计算词向量的最小词频
6. `epochs`：训练时遍历整个数据集的次数

> 注意：
> 1. 训练的时候输入的语料库一定要是字符组成的二维数组，如：[['北', '京', '你', '好'], ['上', '海', '你', '好']]
> 2. 使用模型的时候有一些默认值，可以通过在 Jupyter 里面通过 Word2Vec 查看

下面是个简单的测试样例：

In [17]:
from gensim.models import Word2Vec

doc = [['30760', '157507'],
       ['289197', '63746'],
       ['36162', '168401'],
       ['50644', '36162']]
w2v = Word2Vec(doc, vector_size=12, sg=1, window=2, seed=2020, workers=2, min_count=1, epochs=1)

# 查看'30760'表示的词向量
w2v.wv['30760']

array([ 0.02408178, -0.00102527,  0.08320773, -0.05805062, -0.00330455,
        0.07352284,  0.00942789, -0.05198064, -0.00500923, -0.08016557,
       -0.08009075,  0.07415534], dtype=float32)

skip-gram 和 cbow 的详细原理可以参考下面的博客：

- [word2vec原理(一) CBOW与Skip-Gram模型基础](https://www.cnblogs.com/pinard/p/7160330.html)
- [word2vec原理(二) 基于Hierarchical Softmax的模型](https://www.cnblogs.com/pinard/p/7243513.html)
- [word2vec原理(三) 基于Negative Sampling的模型](https://www.cnblogs.com/pinard/p/7249903.html)

In [20]:
def trian_item_word2vec(click_df: pd.DataFrame, embed_size: int = 64, save_name: str = 'item_w2v_emb.pkl', split_char: str = ' ') -> dict:
    """
    使用 Word2Vec 训练项目的嵌入向量。

    Args:
        click_df (`pd.DataFrame`): 包含用户点击数据的 DataFrame，必须包含 'click_article_id' 和 'click_timestamp' 列。
        embed_size (`int`, optional): 嵌入向量的维度，默认为 64。
        save_name (`str`, optional): 保存嵌入向量的文件名，默认为 'item_w2v_emb.pkl'。
        split_char (`str`, optional): 切分字符，未使用但保留以兼容性，默认为空格。

    Returns:
        `dict`: 返回训练得到的项目嵌入字典，格式为 {item_id: embedding_vector}。
    """
    
    click_df = click_df.sort_values('click_timestamp')  # 按点击时间排序
    click_df['click_article_id'] = click_df['click_article_id'].astype(str)  # 确保文章 ID 为字符串
    
    # 将每个用户的点击文章转换为句子的形式
    docs = click_df.groupby(['user_id'])['click_article_id'].apply(list).reset_index()
    docs = docs['click_article_id'].values.tolist()  # 获取所有用户的点击文章列表

    # 设置日志信息以查看训练进度
    logging.basicConfig(format='%(asctime)s:%(levelname)s:%(message)s', level=logging.INFO)

    # 训练 Word2Vec 模型
    w2v = Word2Vec(docs, vector_size=embed_size, sg=1, window=5, seed=2020, workers=24, min_count=1, epochs=1)
    
    # 将训练得到的向量保存成字典形式
    item_w2v_emb_dict = {k: w2v.wv[k] for k in click_df['click_article_id'] if k in w2v.wv.key_to_index}
    pickle.dump(item_w2v_emb_dict, open(save_name, 'wb'))  # 保存嵌入字典到文件
    
    return item_w2v_emb_dict  # 返回嵌入字典

- 可以通过字典查询对应的 item 的 Embedding

In [60]:
def get_embedding(save_path: str, all_click_df: pd.DataFrame) -> tuple:
    """
    加载项目和用户的嵌入向量，若文件不存在则训练新的嵌入。

    Args:
        save_path (`str`): 嵌入向量文件的保存路径。
        all_click_df (`pd.DataFrame`): 包含所有用户点击数据的 DataFrame，用于训练新的嵌入（如果需要）。

    Returns:
        `tuple`: 返回四个嵌入字典：
            - `item_content_emb_dict`: 项目内容嵌入字典。
            - `item_w2v_emb_dict`: 项目 Word2Vec 嵌入字典。
            - `item_youtube_emb_dict`: 项目 YouTube 嵌入字典。
            - `user_youtube_emb_dict`: 用户 YouTube 嵌入字典。
    """
    # 尝试加载项目内容嵌入
    if os.path.exists(save_path + 'item_content_emb.pkl'):
        item_content_emb_dict = pickle.load(open(save_path + 'item_content_emb.pkl', 'rb'))
    else:
        print('item_content_emb.pkl 文件不存在...')
        item_content_emb_dict = None  # 如果文件不存在，返回 None

    # 尝试加载 Word2Vec 嵌入，如果不存在则训练新的嵌入
    if os.path.exists(save_path + 'item_w2v_emb.pkl'):
        item_w2v_emb_dict = pickle.load(open(save_path + 'item_w2v_emb.pkl', 'rb'))
    else:
        item_w2v_emb_dict = trian_item_word2vec(all_click_df)  # 训练新的 Word2Vec 嵌入
        
    # 尝试加载项目 YouTube 嵌入
    if os.path.exists(save_path + 'item_youtube_emb.pkl'):
        item_youtube_emb_dict = pickle.load(open(save_path + 'item_youtube_emb.pkl', 'rb'))
    else:
        print('item_youtube_emb.pkl 文件不存在...')
        item_youtube_emb_dict = None  # 如果文件不存在，返回 None

    # 尝试加载用户 YouTube 嵌入
    if os.path.exists(save_path + 'user_youtube_emb.pkl'):
        user_youtube_emb_dict = pickle.load(open(save_path + 'user_youtube_emb.pkl', 'rb'))
    else:
        print('user_youtube_emb.pkl 文件不存在...')
        user_youtube_emb_dict = None  # 如果文件不存在，返回 None
    
    return item_content_emb_dict, item_w2v_emb_dict, item_youtube_emb_dict, user_youtube_emb_dict

### 3.6 读取文章信息

In [61]:
def get_article_info_df() -> pd.DataFrame:
    """
    读取文章信息并减少内存占用。

    Returns:
        `pd.DataFrame`: 返回包含文章信息的 DataFrame。
    """
    # 读取文章信息的 CSV 文件
    article_info_df = pd.read_csv(data_path + 'articles.csv')
    
    # 减少 DataFrame 的内存使用
    article_info_df = reduce_mem(article_info_df)
    
    return article_info_df  # 返回文章信息 DataFrame

### 3.7 读取数据

In [9]:
# 这里 offline 的 online 的区别就是验证集是否为空
click_trn, click_val, click_tst, val_ans = get_train_val_tst_data(data_path, offline=False)

-- Mem. usage decreased to 23.34 Mb (69.4% reduction), time spent: 0.00 min


In [25]:
click_trn_hist, click_trn_last = get_hist_and_last_click(click_trn)

if click_val is not None:
    click_val_hist, click_val_last = click_val, val_ans
else:
    click_val_hist, click_val_last = None, None
    
click_tst_hist = click_tst

---

## 4 对训练数据做负采样

通过召回我们将数据转换成三元组的形式（user1, item1, label）的形式，观察发现正负样本差距极度不平衡，我们可以先对负样本进行下采样，下采样的目的一方面缓解了正负样本比例的问题，另一方面也减小了我们做排序特征的压力。

在做负采样的时候又有哪些东西是需要注意的呢？

1. 只对负样本进行下采样（如果有比较好的正样本扩充的方法其实也是可以考虑的）
2. 负采样之后，保证所有的用户和文章仍然出现在采样之后的数据中
3. 下采样的比例可以根据实际情况人为的控制
4. 做完负采样之后，更新此时新的用户召回文章列表，因为后续做特征的时候可能用到相对位置的信息。

其实负采样也可以留在后面做完特征在进行，这里由于做排序特征太慢了，所以把负采样的环节提到前面了。

In [26]:
def recall_dict_2_df(recall_list_dict: dict) -> pd.DataFrame:
    """
    将召回列表字典转换为 DataFrame 格式。

    Args:
        recall_list_dict (`dict`): 包含用户召回列表的字典，格式为 {user_id: {item_id: score}}。

    Returns:
        `pd.DataFrame`: 返回一个 DataFrame，包含用户 ID、相似项目及其得分。
    """
    
    df_row_list = []  # 存储转换后的行数据 [user, item, score]
    
    # 遍历召回列表字典
    for user, recall_list in tqdm(recall_list_dict.items()):
        for item, score in recall_list.items():
            df_row_list.append([user, item, score])  # 添加用户、项目及其得分到列表中
    
    col_names = ['user_id', 'sim_item', 'score']  # 定义列名
    recall_list_df = pd.DataFrame(df_row_list, columns=col_names)  # 创建 DataFrame
    
    return recall_list_df  # 返回转换后的 DataFrame

In [36]:
def neg_sample_recall_data(recall_items_df: pd.DataFrame, sample_rate: float = 0.001) -> pd.DataFrame:
    """
    进行负采样，生成包含正负样本的新数据集。

    Args:
        recall_items_df (`pd.DataFrame`): 包含召回项目的 DataFrame，必须包含 'label' 列（1 表示正样本，0 表示负样本）。
        sample_rate (`float`, optional): 负样本的采样比例，默认为 0.001。

    Returns:
        `pd.DataFrame`: 返回合并后的新数据集，包含正样本和负样本。
    """
    
    # 按标签分离正样本和负样本
    pos_data = recall_items_df[recall_items_df['label'] == 1]
    neg_data = recall_items_df[recall_items_df['label'] == 0]
    
    print('pos_data_num:', len(pos_data), 'neg_data_num:', len(neg_data), 'pos/neg:', len(pos_data) / len(neg_data))
    
    # 定义分组采样函数
    def neg_sample_func(group_df: pd.DataFrame) -> pd.DataFrame:
        neg_num = len(group_df)
        sample_num = max(int(neg_num * sample_rate), 1)  # 确保至少采样一个
        sample_num = min(sample_num, 5)  # 最多不超过 5 个
        return group_df.sample(n=sample_num, replace=True)  # 进行采样
    
    # 对用户进行负采样，确保所有用户都在采样后的数据中
    neg_data_user_sample = neg_data.groupby('user_id', group_keys=False).apply(neg_sample_func)
    # 对文章进行负采样，确保所有文章都在采样后的数据中
    neg_data_item_sample = neg_data.groupby('sim_item', group_keys=False).apply(neg_sample_func)
    
    # 合并用户和文章的负采样数据
    neg_data_new = pd.concat([neg_data_user_sample, neg_data_item_sample])
    # 去重，避免重复选择相同的数据
    neg_data_new = neg_data_new.sort_values(['user_id', 'score']).drop_duplicates(['user_id', 'sim_item'], keep='last')
    
    # 合并正样本和新的负样本数据
    data_new = pd.concat([pos_data, neg_data_new], ignore_index=True)
    
    return data_new  # 返回合并后的新数据集

In [30]:
def get_rank_label_df(recall_list_df: pd.DataFrame, label_df: pd.DataFrame, is_test: bool = False) -> pd.DataFrame:
    """
    为召回数据打标签，标记正样本和负样本。

    Args:
        recall_list_df (`pd.DataFrame`): 包含召回项目的 DataFrame，必须包含 'user_id' 和 'sim_item' 列。
        label_df (`pd.DataFrame`): 包含实际点击数据的 DataFrame，必须包含 'user_id' 和 'click_article_id' 列。
        is_test (`bool`, optional): 指示是否为测试集，默认为 False。

    Returns:
        `pd.DataFrame`: 返回带有标签的召回数据 DataFrame。
    """
    
    # 如果是测试集，则为所有召回项目标记为负样本
    if is_test:
        recall_list_df['label'] = -1  # 用 -1 表示没有标签
        return recall_list_df
    
    # 重命名列以便合并
    label_df = label_df.rename(columns={'click_article_id': 'sim_item'})
    
    # 合并召回数据和标签数据
    recall_list_df_ = recall_list_df.merge(label_df[['user_id', 'sim_item', 'click_timestamp']], 
                                               how='left', on=['user_id', 'sim_item'])
    
    # 根据点击时间戳打标签：存在点击则为正样本（1.0），否则为负样本（0.0）
    recall_list_df_['label'] = recall_list_df_['click_timestamp'].apply(lambda x: 0.0 if np.isnan(x) else 1.0)
    
    # 删除点击时间戳列
    del recall_list_df_['click_timestamp']
    
    return recall_list_df_  # 返回带标签的召回数据

In [31]:
def get_user_recall_item_label_df(click_trn_hist: pd.DataFrame, 
                                   click_val_hist: pd.DataFrame, 
                                   click_tst_hist: pd.DataFrame, 
                                   click_trn_last: pd.DataFrame, 
                                   click_val_last: pd.DataFrame, 
                                   recall_list_df: pd.DataFrame) -> tuple:
    """
    获取用户的召回项目及其标签 DataFrame。

    Args:
        click_trn_hist (`pd.DataFrame`): 训练集点击历史数据。
        click_val_hist (`pd.DataFrame`): 验证集点击历史数据。
        click_tst_hist (`pd.DataFrame`): 测试集点击历史数据。
        click_trn_last (`pd.DataFrame`): 训练集最后一次点击数据。
        click_val_last (`pd.DataFrame`): 验证集最后一次点击数据。
        recall_list_df (`pd.DataFrame`): 包含召回项目的 DataFrame。

    Returns:
        `tuple`: 返回三个 DataFrame：
            - `trn_user_item_label_df`: 训练集用户召回项目及标签。
            - `val_user_item_label_df`: 验证集用户召回项目及标签（可能为 None）。
            - `tst_user_item_label_df`: 测试集用户召回项目及标签。
    """
    
    # 获取训练数据的召回列表
    trn_user_items_df = recall_list_df[recall_list_df['user_id'].isin(click_trn_hist['user_id'].unique())]
    
    # 为训练数据打标签
    trn_user_item_label_df = get_rank_label_df(trn_user_items_df, click_trn_last, is_test=False)
    
    # 进行训练数据的负采样
    trn_user_item_label_df = neg_sample_recall_data(trn_user_item_label_df)
    
    # 如果验证集存在，进行相应处理
    if click_val_hist is not None:
        val_user_items_df = recall_list_df[recall_list_df['user_id'].isin(click_val_hist['user_id'].unique())]
        
        # 为验证数据打标签
        val_user_item_label_df = get_rank_label_df(val_user_items_df, click_val_last, is_test=False)
        
        # 进行验证数据的负采样
        val_user_item_label_df = neg_sample_recall_data(val_user_item_label_df)
    else:
        val_user_item_label_df = None  # 如果没有验证集，返回 None
        
    # 测试数据不需要负采样，直接打 -1 标签
    tst_user_items_df = recall_list_df[recall_list_df['user_id'].isin(click_tst_hist['user_id'].unique())]
    tst_user_item_label_df = get_rank_label_df(tst_user_items_df, None, is_test=True)
    
    return trn_user_item_label_df, val_user_item_label_df, tst_user_item_label_df

In [33]:
# 读取召回列表，这里只选择了单路召回的结果，也可以选择多路召回结果
recall_list_dict = get_recall_list(save_path, multi_recall=True)

In [34]:
# 将召回数据转换成df
recall_list_df = recall_dict_2_df(recall_list_dict)

100%|██████████| 250000/250000 [00:14<00:00, 17230.01it/s]


In [37]:
# 给训练验证数据打标签，并负采样（这一部分时间比较久）
trn_user_item_label_df, val_user_item_label_df, tst_user_item_label_df = get_user_recall_item_label_df(click_trn_hist, 
                                                                                                       click_val_hist, 
                                                                                                       click_tst_hist,
                                                                                                       click_trn_last, 
                                                                                                       click_val_last, 
                                                                                                       recall_list_df)

pos_data_num: 44854 neg_data_num: 21531938 pos/neg: 0.0020831380807431266


In [38]:
trn_user_item_label_df.label

0         1.0
1         1.0
2         1.0
3         1.0
4         1.0
         ... 
402819    0.0
402820    0.0
402821    0.0
402822    0.0
402823    0.0
Name: label, Length: 402824, dtype: float64

---

## 5 将召回数据抓换成字典

In [41]:
def make_tuple_func(group_df: pd.DataFrame) -> list:
    """
    将 DataFrame 的每一行转换为元组格式，提取特定字段。

    Args:
        group_df (`pd.DataFrame`): 输入的 DataFrame，必须包含 'sim_item'、'score' 和 'label' 列。

    Returns:
        `list`: 返回一个元组列表，每个元组包含 (sim_item, score, label)。
    """
    
    row_data = []  # 初始化一个列表以存储元组数据
    
    # 遍历 DataFrame 的每一行
    for _, row_df in group_df.iterrows():
        # 提取所需字段并将其作为元组添加到列表中
        row_data.append((row_df['sim_item'], row_df['score'], row_df['label']))
    
    return row_data  # 返回包含元组的列表

In [42]:
trn_user_item_label_tuples = trn_user_item_label_df.groupby('user_id').apply(make_tuple_func).reset_index()
trn_user_item_label_tuples_dict = dict(zip(trn_user_item_label_tuples['user_id'], trn_user_item_label_tuples[0]))

In [47]:
trn_user_item_label_tuples, trn_user_item_label_tuples_dict

(        user_id                                                  0
 0             0               [(31836.0, 0.1290643121232055, 0.0)]
 1             1  [(19344.0, 0.0, 0.0), (67914.0, 0.002800769931...
 2             2                             [(159634.0, 0.0, 0.0)]
 3             3             [(289003.0, 0.05807153585388918, 0.0)]
 4             4  [(146117.0, 0.004073512793862981, 0.0), (33625...
 ...         ...                                                ...
 199995   199995  [(168623.0, 0.203481391688845, 0.0), (278626.0...
 199996   199996  [(341755.0, 0.08694431902960519, 0.0), (233717...
 199997   199997  [(289003.0, 0.05801956784116099, 0.0), (221949...
 199998   199998  [(1800.0, 0.0008886905160699784, 0.0), (209077...
 199999   199999               [(158622.0, 1.769154259221463, 0.0)]
 
 [200000 rows x 2 columns],
 {0: [(31836.0, 0.1290643121232055, 0.0)],
  1: [(19344.0, 0.0, 0.0), (67914.0, 0.002800769931149237, 0.0)],
  2: [(159634.0, 0.0, 0.0)],
  3: [(289003.0,

In [48]:
if val_user_item_label_df is not None:
    val_user_item_label_tuples = val_user_item_label_df.groupby('user_id').apply(make_tuple_func).reset_index()
    val_user_item_label_tuples_dict = dict(zip(val_user_item_label_tuples['user_id'], val_user_item_label_tuples[0]))
else:
    val_user_item_label_tuples_dict = None

In [54]:
tst_user_item_label_tuples = tst_user_item_label_df.groupby('user_id').apply(make_tuple_func).reset_index()
tst_user_item_label_tuples_dict = dict(zip(tst_user_item_label_tuples['user_id'], tst_user_item_label_tuples[0]))

In [57]:
tst_user_item_label_tuples_dict

{200000: [(195148.0, 2.0, -1.0),
  (191923.0, 2.283874542783442, -1.0),
  (191904.0, 1.273623691931876, -1.0),
  (191911.0, 1.245596481818449, -1.0),
  (191890.0, 1.050286696827806, -1.0),
  (191894.0, 1.0444345429452127, -1.0),
  (191886.0, 1.9314920706702832, -1.0),
  (191907.0, 1.9164600702792354, -1.0),
  (191905.0, 1.0086558251833135, -1.0),
  (191881.0, 1.8878124698160752, -1.0),
  (188747.0, 0.9922735520143696, -1.0),
  (188404.0, 0.9918894801302928, -1.0),
  (188108.0, 0.9859281365288438, -1.0),
  (195428.0, 0.9859278880229603, -1.0),
  (194671.0, 1.3202513778396885, -1.0),
  (194686.0, 0.9857326293221226, -1.0),
  (195199.0, 1.2953498843746045, -1.0),
  (194735.0, 1.2890707661887912, -1.0),
  (188104.0, 0.9853918268505071, -1.0),
  (195508.0, 1.2863384599198242, -1.0),
  (195035.0, 1.0083492526717797, -1.0),
  (188599.0, 0.9810907698436818, -1.0),
  (194920.0, 0.9810826527529557, -1.0),
  (189060.0, 0.9809468865614053, -1.0),
  (188206.0, 0.9809194068023966, -1.0),
  (188395.0

---

## 6 用户历史行为相关特征

对于每个用户召回的每个商品，做特征，获取最后点击的 N 个商品的 item_id。

对于该用户的每个召回商品，计算与上面最后 N 次点击商品的相似度的和（最大， 最小，均值）、时间差特征、相似性特征、字数差特征、与该用户的相似性特征。

In [58]:
def create_feature(users_id: list, 
                   recall_list: dict, 
                   click_hist_df: pd.DataFrame, 
                   articles_info: pd.DataFrame, 
                   articles_emb: dict, 
                   user_emb: dict = None, 
                   N: int = 1) -> pd.DataFrame:
    """
    基于用户的历史行为生成相关特征。

    Args:
        users_id (`list`): 用户 ID 列表。
        recall_list (`dict`): 每个用户召回的候选文章列表，格式为 {user_id: [(article_id, score, label), ...]}。
        click_hist_df (`pd.DataFrame`): 用户的历史点击信息，必须包含 'user_id' 和 'click_article_id' 列。
        articles_info (`pd.DataFrame`): 文章信息，必须包含 'article_id'、'created_at_ts' 和 'words_count' 列。
        articles_emb (`dict`): 文章的嵌入向量，格式为 {article_id: embedding_vector}。
        user_emb (`dict`, optional): 用户的嵌入向量，格式为 {user_id: embedding_vector}，默认为 None。
        N (`int`, optional): 最近的 N 次点击，默认为 1。

    Returns:
        `pd.DataFrame`: 返回包含用户特征的 DataFrame。
    """
    
    # 初始化一个列表以存储所有用户的特征
    all_user_feas = []
    
    # 遍历用户 ID
    for user_id in tqdm(users_id):
        # 获取该用户的最后 N 次点击文章
        hist_user_items = click_hist_df[click_hist_df['user_id'] == user_id]['click_article_id'][-N:]
        
        # 遍历该用户的召回列表
        for rank, (article_id, score, label) in enumerate(recall_list[user_id]):
            # 获取文章的创建时间和字数
            a_create_time = articles_info[articles_info['article_id'] == article_id]['created_at_ts'].values[0]
            a_words_count = articles_info[articles_info['article_id'] == article_id]['words_count'].values[0]
            single_user_fea = [user_id, article_id]  # 初始化特征列表
            
            # 初始化相似性、时间和字数差特征列表
            sim_fea, time_fea, word_fea = [], [], []
            
            # 遍历用户的最后 N 次点击文章
            for hist_item in hist_user_items:
                b_create_time = articles_info[articles_info['article_id'] == hist_item]['created_at_ts'].values[0]
                b_words_count = articles_info[articles_info['article_id'] == hist_item]['words_count'].values[0]
                
                # 计算特征
                sim_fea.append(np.dot(articles_emb[hist_item], articles_emb[article_id]))  # 相似度
                time_fea.append(abs(a_create_time - b_create_time))  # 时间差
                word_fea.append(abs(a_words_count - b_words_count))  # 字数差
            
            # 将计算得到的特征添加到总特征列表中
            single_user_fea.extend(sim_fea)  # 相似性特征
            single_user_fea.extend(time_fea)  # 时间差特征
            single_user_fea.extend(word_fea)  # 字数差特征
            single_user_fea.extend([max(sim_fea), min(sim_fea), sum(sim_fea), sum(sim_fea) / len(sim_fea)])  # 相似性的统计特征
            
            if user_emb:  # 如果用户向量存在，计算用户与文章的相似性
                single_user_fea.append(np.dot(user_emb[user_id], articles_emb[article_id]))
                
            single_user_fea.extend([score, rank, label])  # 加入评分、排名和标签
            
            # 添加单个用户的特征到总列表中
            all_user_feas.append(single_user_fea)
    
    # 定义列名
    id_cols = ['user_id', 'click_article_id']
    sim_cols = ['sim' + str(i) for i in range(N)]
    time_cols = ['time_diff' + str(i) for i in range(N)]
    word_cols = ['word_diff' + str(i) for i in range(N)]
    sat_cols = ['sim_max', 'sim_min', 'sim_sum', 'sim_mean']
    user_item_sim_cols = ['user_item_sim'] if user_emb else []
    user_score_rank_label = ['score', 'rank', 'label']
    
    # 合并所有列名
    cols = id_cols + sim_cols + time_cols + word_cols + sat_cols + user_item_sim_cols + user_score_rank_label
            
    # 转换为 DataFrame
    df = pd.DataFrame(all_user_feas, columns=cols)
    
    return df  # 返回特征 DataFrame

In [59]:
article_info_df = get_article_info_df()
all_click = pd.concat([click_trn, click_tst], ignore_index=True)
item_content_emb_dict, item_w2v_emb_dict, item_youtube_emb_dict, user_youtube_emb_dict = get_embedding(save_path, all_click)

-- Mem. usage decreased to  5.56 Mb (50.0% reduction), time spent: 0.00 min


In [62]:
# 获取训练验证及测试数据中召回列文章相关特征
trn_user_item_feats_df = create_feature(trn_user_item_label_tuples_dict.keys(), trn_user_item_label_tuples_dict, \
                                            click_trn_hist, article_info_df, item_content_emb_dict)

100%|██████████| 200000/200000 [14:45<00:00, 225.86it/s]


In [63]:
if val_user_item_label_tuples_dict is not None:
    val_user_item_feats_df = create_feature(val_user_item_label_tuples_dict.keys(), val_user_item_label_tuples_dict, \
                                                click_val_hist, article_info_df, item_content_emb_dict)
else:
    val_user_item_feats_df = None

In [64]:
tst_user_item_feats_df = create_feature(tst_user_item_label_tuples_dict.keys(), tst_user_item_label_tuples_dict, \
                                            click_tst_hist, article_info_df, item_content_emb_dict)

  0%|          | 166/50000 [00:34<2:42:40,  5.11it/s]

: 

In [67]:
# 保存一份省的每次都要重新跑，每次跑的时间都比较长
trn_user_item_feats_df.to_csv(save_path + 'trn_user_item_feats_df.csv', index=False)

if val_user_item_feats_df is not None:
    val_user_item_feats_df.to_csv(save_path + 'val_user_item_feats_df.csv', index=False)

tst_user_item_feats_df.to_csv(save_path + 'tst_user_item_feats_df.csv', index=False)    

---

## 7 用户和文章特征

### 7.1 用户相关特征

这一块，正式进行特征工程，既要拼接上已有的特征，也会做更多的特征出来，我们来梳理一下已有的特征和可构造特征：

1. 文章自身的特征，文章字数，文章创建时间，文章的 embedding （articles 表中)
2. 用户点击环境特征，那些设备的特征（这个在 df 中）
3. 对于用户和商品还可以构造的特征：
   * 基于用户的点击文章次数和点击时间构造可以表现用户活跃度的特征
   * 基于文章被点击次数和时间构造可以反映文章热度的特征
   * 用户的时间统计特征：根据其点击的历史文章列表的点击时间和文章的创建时间做统计特征，比如求均值，这个可以反映用户对于文章时效的偏好
   * 用户的主题爱好特征，对于用户点击的历史文章主题进行一个统计，然后对于当前文章看看是否属于用户已经点击过的主题
   * 用户的字数爱好特征，对于用户点击的历史文章的字数统计，求一个均值

In [10]:
click_tst.head()

user_id  click_article_id  click_timestamp  click_environment  \
0   249999            160974    1506959142820                  4   
1   249999            160417    1506959172820                  4   
2   249998            160974    1506959056066                  4   
3   249998            202557    1506959086066                  4   
4   249997            183665    1506959088613                  4   

   click_deviceGroup  click_os  click_country  click_region  \
0                  1        17              1            13   
1                  1        17              1            13   
2                  1        12              1            13   
3                  1        12              1            13   
4                  1        17              1            15   

   click_referrer_type  
0                    2  
1                    2  
2                    2  
3                    2  
4                    5

In [11]:
# 读取文章特征
articles =  pd.read_csv(data_path+'articles.csv')
articles = reduce_mem(articles)

# 日志数据，就是前面的所有数据
if click_val is not None:
    all_data = pd.concat([click_trn, click_val], ignore_index=True)
all_data = pd.concat([click_trn, click_tst], ignore_index=True)
all_data = reduce_mem(all_data)

# 拼上文章信息
all_data = all_data.merge(articles, left_on='click_article_id', right_on='article_id')

-- Mem. usage decreased to  5.56 Mb (50.0% reduction), time spent: 0.00 min
-- Mem. usage decreased to 34.21 Mb (69.4% reduction), time spent: 0.00 min


In [12]:
all_data.shape

(1630633, 13)

**分析一下点击时间和点击文章的次数，区分用户活跃度**

如果某个用户点击文章之间的时间间隔比较小，同时点击的文章次数很多的话，那么我们认为这种用户一般就是活跃用户，当然衡量用户活跃度的方式可能多种多样，这里我们只提供其中一种，我们写一个函数，得到可以衡量用户活跃度的特征，逻辑如下：

1. 首先根据用户 user_id 分组，对于每个用户，计算点击文章的次数，两两点击文章时间间隔的均值
2. 把点击次数取倒数和时间间隔的均值统一归一化，然后两者相加合并，该值越小，说明用户越活跃
3. 注意，上面两两点击文章的时间间隔均值，会出现如果用户只点击了一次的情况，这时候时间间隔均值那里会出现空值，对于这种情况最后特征那里给个大数进行区分

这个的衡量标准就是先把点击的次数取到数然后归一化，然后点击的时间差归一化，然后两者相加进行合并，该值越小，说明被点击的次数越多，且间隔时间短。 

In [14]:
def active_level(all_data: pd.DataFrame, cols: list) -> pd.DataFrame:
    """
    制作区分用户活跃度的特征。

    Args:
        all_data (`pd.DataFrame`): 输入的数据集，必须包含 'user_id'、'click_article_id' 和 'click_timestamp' 列。
        cols (`list`): 使用的特征列列表。

    Returns:
        `pd.DataFrame`: 返回包含用户活跃度特征的 DataFrame。
    """
    # 选择需要的特征列并按用户 ID 和点击时间排序
    data = all_data[cols]
    data.sort_values(['user_id', 'click_timestamp'], inplace=True)
    
    # 计算每个用户的点击次数和点击时间戳列表
    user_act = pd.DataFrame(
        data.groupby('user_id', as_index=False)[['click_article_id', 'click_timestamp']]
        .agg({'click_article_id': np.size, 'click_timestamp': {list}}).values,
        columns=['user_id', 'click_size', 'click_timestamp']
    )
    
    # 计算时间间隔的均值
    def time_diff_mean(l):
        if len(l) == 1:
            return 1  # 如果只有一次点击，返回 1
        else:
            return np.mean([j - i for i, j in zip(l[:-1], l[1:])])  # 计算时间差均值
    
    user_act['time_diff_mean'] = user_act['click_timestamp'].apply(lambda x: time_diff_mean(x))
    
    # 点击次数取倒数，以便进行归一化
    user_act['click_size'] = 1 / user_act['click_size']
    
    # 对点击次数和时间间隔均值进行归一化
    user_act['click_size'] = (user_act['click_size'] - user_act['click_size'].min()) / (user_act['click_size'].max() - user_act['click_size'].min())
    user_act['time_diff_mean'] = (user_act['time_diff_mean'] - user_act['time_diff_mean'].min()) / (user_act['time_diff_mean'].max() - user_act['time_diff_mean'].min())
    
    # 计算活跃度特征
    user_act['active_level'] = user_act['click_size'] + user_act['time_diff_mean']
    
    # 将用户 ID 转换为整数类型，并删除点击时间戳列
    user_act['user_id'] = user_act['user_id'].astype('int')
    del user_act['click_timestamp']
    
    return user_act  # 返回用户活跃度特征 DataFrame

In [15]:
user_act_fea = active_level(all_data, ['user_id', 'click_article_id', 'click_timestamp'])

In [16]:
user_act_fea.head()

user_id click_size  time_diff_mean active_level
0        0   0.499466        0.000048     0.499515
1        1   0.499466        0.000048     0.499515
2        2   0.499466        0.000048     0.499515
3        3   0.499466        0.000048     0.499515
4        4   0.499466        0.000048     0.499515

In [18]:
def hot_level(all_data: pd.DataFrame, cols: list) -> pd.DataFrame:
    """
    制作衡量文章热度的特征。

    Args:
        all_data (`pd.DataFrame`): 输入的数据集，必须包含 'click_article_id'、'user_id' 和 'click_timestamp' 列。
        cols (`list`): 使用的特征列列表。

    Returns:
        `pd.DataFrame`: 返回包含文章热度特征的 DataFrame。
    """
    # 选择需要的特征列并按文章 ID 和点击时间排序
    data = all_data[cols]
    data.sort_values(['click_article_id', 'click_timestamp'], inplace=True)
    
    # 计算每篇文章的用户点击数和点击时间戳列表
    article_hot = pd.DataFrame(
        data.groupby('click_article_id', as_index=False)[['user_id', 'click_timestamp']]
        .agg({'user_id': np.size, 'click_timestamp': {list}}).values,
        columns=['click_article_id', 'user_num', 'click_timestamp']
    )
    
    # 计算被点击时间间隔的均值
    def time_diff_mean(l):
        if len(l) == 1:
            return 1  # 如果只有一次点击，返回 1
        else:
            return np.mean([j - i for i, j in zip(l[:-1], l[1:])])  # 计算时间差均值
    
    article_hot['time_diff_mean'] = article_hot['click_timestamp'].apply(lambda x: time_diff_mean(x))
    
    # 用户点击次数取倒数，以便进行归一化
    article_hot['user_num'] = 1 / article_hot['user_num']
    
    # 对用户点击次数和时间间隔均值进行归一化
    article_hot['user_num'] = (article_hot['user_num'] - article_hot['user_num'].min()) / (article_hot['user_num'].max() - article_hot['user_num'].min())
    article_hot['time_diff_mean'] = (article_hot['time_diff_mean'] - article_hot['time_diff_mean'].min()) / (article_hot['time_diff_mean'].max() - article_hot['time_diff_mean'].min())
    
    # 计算文章热度特征
    article_hot['hot_level'] = article_hot['user_num'] + article_hot['time_diff_mean']
    
    # 将文章 ID 转换为整数类型，并删除点击时间戳列
    article_hot['click_article_id'] = article_hot['click_article_id'].astype('int')
    del article_hot['click_timestamp']
    
    return article_hot  # 返回文章热度特征 DataFrame

In [19]:
article_hot_fea = hot_level(all_data, ['user_id', 'click_article_id', 'click_timestamp'])    

In [20]:
article_hot_fea.head()

click_article_id user_num  time_diff_mean hot_level
0                 3      1.0             0.0       1.0
1                69      1.0             0.0       1.0
2                84      1.0             0.0       1.0
3                94      1.0             0.0       1.0
4               125      1.0             0.0       1.0

In [21]:
def device_fea(all_data: pd.DataFrame, cols: list) -> pd.DataFrame:
    """
    制作用户的设备特征。

    Args:
        all_data (`pd.DataFrame`): 输入的数据集，必须包含 'user_id' 和设备特征列。
        cols (`list`): 使用的特征列列表。

    Returns:
        `pd.DataFrame`: 返回包含每个用户设备特征的 DataFrame。
    """
    # 选择用户设备信息的特征列
    user_device_info = all_data[cols]
    
    # 用众数来表示每个用户的设备信息
    user_device_info = user_device_info.groupby('user_id').agg(lambda x: x.value_counts().index[0]).reset_index()
    
    return user_device_info  # 返回用户设备特征 DataFrame

In [22]:
# 设备特征(这里时间会比较长)
device_cols = ['user_id', 'click_environment', 'click_deviceGroup', 'click_os', 'click_country', 'click_region', 'click_referrer_type']
user_device_info = device_fea(all_data, device_cols)

In [23]:
user_device_info.head()

user_id  click_environment  click_deviceGroup  click_os  click_country  \
0        0                  4                  1        17              1   
1        1                  4                  1        17              1   
2        2                  4                  3        20              1   
3        3                  4                  3         2              1   
4        4                  4                  1        12              1   

   click_region  click_referrer_type  
0            25                    2  
1            25                    6  
2            25                    2  
3            25                    2  
4            16                    1

In [24]:
def user_time_hob_fea(all_data: pd.DataFrame, cols: list) -> pd.DataFrame:
    """
    制作用户的时间习惯特征。

    Args:
        all_data (`pd.DataFrame`): 输入的数据集，必须包含 'user_id'、'click_timestamp' 和 'created_at_ts' 列。
        cols (`list`): 使用的特征列列表。

    Returns:
        `pd.DataFrame`: 返回包含用户时间习惯特征的 DataFrame。
    """
    
    # 选择用户时间习惯信息的特征列
    user_time_hob_info = all_data[cols]
    
    # 先对时间戳进行归一化处理
    mm = MinMaxScaler()
    user_time_hob_info['click_timestamp'] = mm.fit_transform(user_time_hob_info[['click_timestamp']])
    user_time_hob_info['created_at_ts'] = mm.fit_transform(user_time_hob_info[['created_at_ts']])

    # 按用户 ID 计算时间戳的均值
    user_time_hob_info = user_time_hob_info.groupby('user_id').agg('mean').reset_index()
    
    # 重命名列以表示用户时间习惯特征
    user_time_hob_info.rename(columns={'click_timestamp': 'user_time_hob1', 'created_at_ts': 'user_time_hob2'}, inplace=True)
    
    return user_time_hob_info  # 返回用户时间习惯特征 DataFrame

In [25]:
user_time_hob_cols = ['user_id', 'click_timestamp', 'created_at_ts']
user_time_hob_info = user_time_hob_fea(all_data, user_time_hob_cols)

In [26]:
def user_cat_hob_fea(all_data: pd.DataFrame, cols: list) -> pd.DataFrame:
    """
    制作用户的主题爱好特征。

    Args:
        all_data (`pd.DataFrame`): 输入的数据集，必须包含 'user_id' 和 'category_id' 列。
        cols (`list`): 使用的特征列列表。

    Returns:
        `pd.DataFrame`: 返回包含用户主题爱好的 DataFrame。
    """
    
    # 选择用户主题爱好信息的特征列
    user_category_hob_info = all_data[cols]
    
    # 按用户 ID 分组并聚合类别信息为列表
    user_category_hob_info = user_category_hob_info.groupby('user_id').agg(lambda x: list(x)).reset_index()
    
    # 创建新的 DataFrame 以存储用户及其类别列表
    user_cat_hob_info = pd.DataFrame()
    user_cat_hob_info['user_id'] = user_category_hob_info['user_id']
    user_cat_hob_info['cate_list'] = user_category_hob_info['category_id']
    
    return user_cat_hob_info  # 返回用户主题爱好特征 DataFrame

In [27]:
user_category_hob_cols = ['user_id', 'category_id']
user_cat_hob_info = user_cat_hob_fea(all_data, user_category_hob_cols)

In [28]:
user_wcou_info = all_data.groupby('user_id')['words_count'].agg('mean').reset_index()
user_wcou_info.rename(columns={'words_count': 'words_hbo'}, inplace=True)

In [29]:
# 所有表进行合并
user_info = pd.merge(user_act_fea, user_device_info, on='user_id')
user_info = user_info.merge(user_time_hob_info, on='user_id')
user_info = user_info.merge(user_cat_hob_info, on='user_id')
user_info = user_info.merge(user_wcou_info, on='user_id')

In [30]:
# 这样用户特征以后就可以直接读取了
user_info.to_csv(save_path + 'user_info.csv', index=False)   

In [5]:
# 把用户信息直接读入进来
user_info = pd.read_csv(save_path + 'user_info.csv')

In [ ]:
if os.path.exists(save_path + 'trn_user_item_feats_df.csv'):
    trn_user_item_feats_df = pd.read_csv(save_path + 'trn_user_item_feats_df.csv')

if os.path.exists(save_path + 'tst_user_item_feats_df.csv'):
    tst_user_item_feats_df = pd.read_csv(save_path + 'tst_user_item_feats_df.csv')

if os.path.exists(save_path + 'val_user_item_feats_df.csv'):
    val_user_item_feats_df = pd.read_csv(save_path + 'val_user_item_feats_df.csv')
else:
    val_user_item_feats_df = None

In [8]:
# 拼上用户特征
# 下面是线下验证的
trn_user_item_feats_df = trn_user_item_feats_df.merge(user_info, on='user_id', how='left')

if val_user_item_feats_df is not None:
    val_user_item_feats_df = val_user_item_feats_df.merge(user_info, on='user_id', how='left')
else:
    val_user_item_feats_df = None
    
tst_user_item_feats_df = tst_user_item_feats_df.merge(user_info, on='user_id',how='left')

MergeError: Passing 'suffixes' which cause duplicate columns {'click_environment_x', 'user_time_hob1_x', 'click_deviceGroup_x', 'time_diff_mean_x', 'words_hbo_x', 'click_referrer_type_x', 'click_country_x', 'click_size_x', 'user_time_hob2_x', 'active_level_x', 'click_region_x', 'click_os_x'} is not allowed.

In [ ]:
trn_user_item_feats_df.columns

Index(['user_id', 'click_article_id', 'sim0', 'time_diff0', 'word_diff0',
       'sim_max', 'sim_min', 'sim_sum', 'sim_mean', 'score', 'rank', 'label',
       'click_size_x', 'time_diff_mean_x', 'active_level_x',
       'click_environment_x', 'click_deviceGroup_x', 'click_os_x',
       'click_country_x', 'click_region_x', 'click_referrer_type_x',
       'user_time_hob1_x', 'user_time_hob2_x', 'words_hbo_x', 'category_id',
       'created_at_ts', 'words_count', 'is_cat_hab', 'click_size_y',
       'time_diff_mean_y', 'active_level_y', 'click_environment_y',
       'click_deviceGroup_y', 'click_os_y', 'click_country_y',
       'click_region_y', 'click_referrer_type_y', 'user_time_hob1_y',
       'user_time_hob2_y', 'cate_list', 'words_hbo_y'],
      dtype='object')

In [ ]:
articles =  pd.read_csv(data_path +'articles.csv')
articles = reduce_mem(articles)

-- Mem. usage decreased to  5.56 Mb (50.0% reduction), time spent: 0.00 min


In [44]:
# 拼上文章特征
trn_user_item_feats_df = trn_user_item_feats_df.merge(articles, left_on='click_article_id', right_on='article_id')

if val_user_item_feats_df is not None:
    val_user_item_feats_df = val_user_item_feats_df.merge(articles, left_on='click_article_id', right_on='article_id')
else:
    val_user_item_feats_df = None

tst_user_item_feats_df = tst_user_item_feats_df.merge(articles, left_on='click_article_id', right_on='article_id')

In [45]:
trn_user_item_feats_df['is_cat_hab'] = trn_user_item_feats_df.apply(lambda x: 1 if x.category_id in set(x.cate_list) else 0, axis=1)
if val_user_item_feats_df is not None:
    val_user_item_feats_df['is_cat_hab'] = val_user_item_feats_df.apply(lambda x: 1 if x.category_id in set(x.cate_list) else 0, axis=1)
else:
    val_user_item_feats_df = None
tst_user_item_feats_df['is_cat_hab'] = tst_user_item_feats_df.apply(lambda x: 1 if x.category_id in set(x.cate_list) else 0, axis=1)

AttributeError: 'Series' object has no attribute 'category_id'

In [46]:
# 线下验证
del trn_user_item_feats_df['cate_list']

if val_user_item_feats_df is not None:
    del val_user_item_feats_df['cate_list']
else:
    val_user_item_feats_df = None
    
del tst_user_item_feats_df['cate_list']

del trn_user_item_feats_df['article_id']

if val_user_item_feats_df is not None:
    del val_user_item_feats_df['article_id']
else:
    val_user_item_feats_df = None
    
del tst_user_item_feats_df['article_id']

In [47]:
# 训练验证特征
trn_user_item_feats_df.to_csv(save_path + 'trn_user_item_feats_df.csv', index=False)
if val_user_item_feats_df is not None:
    val_user_item_feats_df.to_csv(save_path + 'val_user_item_feats_df.csv', index=False)
tst_user_item_feats_df.to_csv(save_path + 'tst_user_item_feats_df.csv', index=False)